# Summary

**Key point**

1 . Here Transition rate btw R_0 and R_inf vary with time Find with Help of **Grid Search**

    Day 1,3,5
    alpha = -1.0

    Day 7
    alpha = -0.75

    Day 10,14
    alpha = -0.5

    Day 21
    alpha = -0.2

    Day 28
    alpha = -0.1
2. R_0 and R_inf also vary with time they are in **8 hrs** period Find with Help of **Grid Search**

   **R_0(days)**
   
    Day 1 3 5 7= 3

    Day 10 = 6

    Day 14 21 = 6

    Day 28 = 9

    **R_inf(days)**
   
    Day 1 3 5 7 = 30
    
    Day 10 = 45

    Day 14 = 45

    Day 21 28 = 45

3. **Predicted Funding Rate**(average), **delta** is in form of Annualised form for day **1 3 5 7 10 14 21 28** days and ann factor is **3*365**

4. Connect Model with **ornstein uhlenbeck model** which have three parameters as **kappa** , **theta** , **sigma**

   Here **Theta** is equal to **mean** From previous Model

   Here **kappa** is equal to **1.4**  as we find Half time of 2.0 use to find mean reversion Rate For Tenor **1 3 5 7 10**

   Here **kappa** is equal to **0.4**  as we find Half time of 2.0 use to find mean reversion Rate For Tenor **14 21 28**

   Here **Sigma** is equal to **From basis of perp and spot** take **8hr interval** and last **5 day std dev**  

5. For **day 7,10,14,21,28** we use  combination of both as stated above but for **Day 1,3,5** use simple Model with Parameters
   


# Varaiable in Model used Represent What
**T**=Represent Every 8 hrs period means for Day 1 (T=3)

**alpha_estimate**=Represent Transition Rate btween R_0 and R_inf different for for different Day prediction

**half time**=Mean reversion time use **2.0**

# General
1. In perpetual There is 286 approx perpetual contract
2. Create **DASHBOARD** for predection ,Absolute delta , correlation, beta,Relative Delta
3. df_symbol datframe all perp symbol
4. Genralised function is there Run that automatically create csv for all contracts






# Model  Limitation 
We need to Check Funding Rate History If it is Stable Then in Projection are correct No assumption Need to take


If it is Not Stable Then Model Projection Always Below Actual Projection Then we can assume our original Funding Rate is (15%-20%)  above of Projected Funding Rate  But we need To see if historically that Average Funding Rate Is going up or Down if it is going up then projection is below if it is down side then projection is above

If according To Model we Make  Money then we More Probabiltiy That  we Don't Lose any Money
 
# Note
Model created For Normal Funding Rate if Rate is Exceptionally High Then we Need assume according to that about how Much it is above The projected Funding Rate if funding is normal then assume small delta(How much above or Below) for projected  if high then High delta(How much above or below)

In [1]:
#install Important Packages
!pip install seaborn
!pip install scikit-learn
!pip install ccxt
!pip install pytz


[notice] A new release of pip is available: 23.3.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip



[notice] A new release of pip is available: 23.3.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip



[notice] A new release of pip is available: 23.3.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip



[notice] A new release of pip is available: 23.3.1 -> 24.0
[notice] To update, run: python.exe -m pip install --upgrade pip


# Import important Library

In [15]:
#import important Library
import ccxt
import pandas as pd
import numpy as np
import datetime
import matplotlib.pyplot as plt
from datetime import datetime, timedelta
from sklearn.preprocessing import MinMaxScaler

In [16]:
import numpy as np
import scipy as scp
import scipy.stats as ss
from scipy.optimize import minimize
import matplotlib.pyplot as plt
from scipy import sparse
from scipy.sparse.linalg import spsolve
from mpl_toolkits import mplot3d
from matplotlib import cm
import scipy.special as scsp
from scipy.integrate import quad
# from FMNM.Processes import OU_process
from scipy.interpolate import RegularGridInterpolator

In [17]:
#Loads Market Datam of binance
binance=ccxt.binance({'verbose': True})
binance_markets = binance.load_markets()
df=pd.DataFrame(binance_markets)
# print market data for all Financail assest


fetch Request: binance GET https://api.binance.com/api/v3/exchangeInfo RequestHeaders: {'User-Agent': 'python-requests/2.31.0', 'Accept-Encoding': 'gzip, deflate', 'Accept': '*/*', 'Connection': 'keep-alive'} RequestBody: None

fetch Response: binance GET https://api.binance.com/api/v3/exchangeInfo 200 ResponseHeaders: {'Content-Type': 'application/json;charset=UTF-8', 'Content-Length': '102541', 'Connection': 'keep-alive', 'Date': 'Tue, 14 May 2024 13:46:21 GMT', 'Server': 'nginx', 'x-mbx-uuid': 'b2afea45-bace-41c9-a40c-79a53c5b7746', 'x-mbx-used-weight': '20', 'x-mbx-used-weight-1m': '20', 'content-encoding': 'gzip', 'Strict-Transport-Security': 'max-age=31536000; includeSubdomains', 'X-Frame-Options': 'SAMEORIGIN', 'X-Xss-Protection': '1; mode=block', 'X-Content-Type-Options': 'nosniff', 'Content-Security-Policy': "default-src 'self'", 'X-Content-Security-Policy': "default-src 'self'", 'X-WebKit-CSP': "default-src 'self'", 'Cache-Control': 'no-cache, no-store, must-revalidate', 'Pr

# From Here we can Handle How many symbol want to projected

In [5]:
# Creating a DataFrame
data = {'symbol': ['NEAR/USDT:USDT']}
df_t_1 = pd.DataFrame(data)

# Displaying the DataFrame
print(df_t_1)

           symbol
0  NEAR/USDT:USDT


# Collection of all Symbol present in CCxt Library 

In [18]:
# transpose Dataframe
df_t =df.T

# Taking assest which have swap==True
df_t_1 =df_t[df_t["swap"]]
df_t_1= df_t_1.reset_index(drop=True)
df_t_1 = df_t_1.iloc[:1]

# print assest which have prepetual swap contract
df_t_1

id lowercaseId         symbol base quote settle baseId quoteId  \
0  BTCUSDT     btcusdt  BTC/USDT:USDT  BTC  USDT   USDT    BTC    USDT   

  settleId  type  ... expiryDatetime strike optionType  \
0     USDT  swap  ...           None   None       None   

                                           precision  \
0  {'amount': 3, 'price': 1, 'cost': None, 'base'...   

                                              limits        created  \
0  {'leverage': {'min': None, 'max': None}, 'amou...  1569398400000   

                                                info percentage feeSide  \
0  {'symbol': 'BTCUSDT', 'pair': 'BTCUSDT', 'cont...       True     get   

  tierBased  
0     False  

[1 rows x 35 columns]

In [53]:
#Storing id of Prepetual Contract
df_id=df_t_1['id']
df_id

0    BTCUSDT
Name: id, dtype: object

In [19]:
#Storing Symbol of Prepetual Contract
df_symbol=df_t_1['symbol']
df_symbol

0    BTC/USDT:USDT
Name: symbol, dtype: object

# Funding Rate Reterival Function

In [20]:
#Function to fetch Funding Rate
def getFundingRate(symbol):

# We can Change exchange Name
    exchange_name = 'binance'
    exchange = getattr(ccxt, exchange_name)()


    start_date = datetime.now() - timedelta(days=100)
    since = int(start_date.timestamp()) * 1000
# Fetch historical trading data form current Time upto last 250 Values
    funding_rates = exchange.fetchFundingRateHistory(symbol, since=since, limit=300) #take step size of 8hrs

# convert funding_rates into Dataframe
    df=pd.DataFrame(funding_rates)

# dropping column info symbol timestamp from Dataframe
    df=df.drop(['info'], axis=1)
    df=df.drop(['symbol'], axis=1)
    # df=df.drop(['timestamp'], axis=1)

# convert funding rate to percentage
    df['fundingRate']=df['fundingRate']*100

# truncate funding rate upto for decimal
    df['fundingRate'] = df['fundingRate'].round(decimals=4)
    # print(df)

    return df

# Function to Fetch Price History of Given Symbol

In [21]:
#Genral code for Fetch price History on basis of symbol
def fetch_price_history(symbol, timeframe='8h', limit=300):

        from datetime import datetime, timezone

        exchange_name = 'binance'
        exchange = getattr(ccxt, exchange_name)()

        start_date = datetime.now() - timedelta(days=100)
        since = int(start_date.timestamp()) * 1000

        # Fetch OHLCV (Open, High, Low, Close, Volume) data
        ohlcv = exchange.fetch_ohlcv(symbol, timeframe, since=since, limit=limit)

        # Convert the OHLCV data to a DataFrame
        df = pd.DataFrame(ohlcv, columns=['timestamp', 'open', 'high', 'low', 'close', 'volume'])
        # print(df)

        return df

# Combine DataPoints in one Dataframe

In [22]:
#Tranversing over every Perpetual contract
df_list=[]
i=0
for symbol in df_symbol:
   
    #Fetch index of this ':' in given symbol 
    colon_index = symbol.find(":")
    df=getFundingRate(symbol)

    #fetch swap History data for SYMBOL
    df_1=fetch_price_history(symbol)
    df_swap = df_1[['close']]
    df_swap = df_swap.rename(columns={'close':'index_price'})
    # df_price=df_swap['close'] 
    
    #fetch spot History data for SYMBOL
    df_1=fetch_price_history(symbol[:colon_index])
    df_spot = df_1[['close']]
    df_spot = df_spot.rename(columns={'close':'mark_price'})
    # df_price_1=df_swap['close']

    # Concatenate the DataFrames along columns
    combined_df = pd.concat([df, df_swap, df_spot], axis=1)

    df_list.append(combined_df)
    print(i)
    i=i+1
# Concatenate the DataFrames along rows and add ID column as the first column
combined_df = pd.concat([pd.concat([pd.DataFrame({'symbol': [id_] * len(df)}), df], axis=1) for df, id_ in zip(df_list, df_symbol)], ignore_index=True)

# Print the combined DataFrame
print(combined_df)

combined_df.to_csv('Funding_Rate_Data.csv')

0
            symbol  fundingRate      timestamp                  datetime  \
0    BTC/USDT:USDT       0.0100  1707062400000  2024-02-04T16:00:00.000Z   
1    BTC/USDT:USDT       0.0100  1707091200000  2024-02-05T00:00:00.000Z   
2    BTC/USDT:USDT       0.0100  1707120000000  2024-02-05T08:00:00.000Z   
3    BTC/USDT:USDT       0.0100  1707148800000  2024-02-05T16:00:00.000Z   
4    BTC/USDT:USDT       0.0100  1707177600000  2024-02-06T00:00:00.000Z   
..             ...          ...            ...                       ...   
295  BTC/USDT:USDT       0.0100  1715558400001  2024-05-13T00:00:00.001Z   
296  BTC/USDT:USDT       0.0085  1715587200001  2024-05-13T08:00:00.001Z   
297  BTC/USDT:USDT       0.0092  1715616000000  2024-05-13T16:00:00.000Z   
298  BTC/USDT:USDT       0.0099  1715644800000  2024-05-14T00:00:00.000Z   
299  BTC/USDT:USDT       0.0100  1715673600000  2024-05-14T08:00:00.000Z   

     index_price  mark_price  
0        42570.3    42582.88  
1        43059.0    430

# Read Csv file From which WE get Data

In [23]:
# Replace 'Funding_Rate_Data.csv' with the path to your CSV file
file_path = 'Funding_Rate_Data.csv'

# Read the CSV file into a DataFrame
df = pd.read_csv(file_path)
 
print(df)

     Unnamed: 0         symbol  fundingRate      timestamp  \
0             0  BTC/USDT:USDT       0.0100  1707062400000   
1             1  BTC/USDT:USDT       0.0100  1707091200000   
2             2  BTC/USDT:USDT       0.0100  1707120000000   
3             3  BTC/USDT:USDT       0.0100  1707148800000   
4             4  BTC/USDT:USDT       0.0100  1707177600000   
..          ...            ...          ...            ...   
295         295  BTC/USDT:USDT       0.0100  1715558400001   
296         296  BTC/USDT:USDT       0.0085  1715587200001   
297         297  BTC/USDT:USDT       0.0092  1715616000000   
298         298  BTC/USDT:USDT       0.0099  1715644800000   
299         299  BTC/USDT:USDT       0.0100  1715673600000   

                     datetime  index_price  mark_price  
0    2024-02-04T16:00:00.000Z      42570.3    42582.88  
1    2024-02-05T00:00:00.000Z      43059.0    43071.88  
2    2024-02-05T08:00:00.000Z      42629.7    42644.03  
3    2024-02-05T16:00:00.00

# Group Data Frame By Symbol

In [24]:
# Group by symbol
df=df.groupby('symbol')

## ENTER DATE FORM WHICH YOU WANT TO PROJECT

In [15]:
# # EXAMPle how to fill
# start_date = datetime(year=2024, month=2, day=20, hour=2, minute=18,second=30)  # Example start date

# Define start date with minute column
start_date = datetime(year=****, month=**, day=**, hour=**, minute=**,second=**)  # Assuming 00:00 hours

# Convert start and end dates to Unix timestamp format
start_timestamp = int(datetime.timestamp(start_date))

#Print current timestamp
print(start_timestamp)


SyntaxError: invalid syntax (2301567238.py, line 5)

## RUN WHEN YOU WANT TO PROJECT ON CUURENT TIMESTAMP

In [25]:
from datetime import datetime

# Get current timestamp
start_timestamp = datetime.now()

# Convert to Unix time
start_timestamp = int(start_timestamp.timestamp())


#Print current timestamp
print(start_timestamp)


1715694493


# For Cleaning Of Dataset

In [26]:
#Tranversing over every Perpetual contract
df_final={}
for symbol, group in df:

    ##------ take name according to column name given in database------###
    df1=group[['timestamp','fundingRate','mark_price','index_price']]
    
    # Rename the columns
    df1 = df1.rename(columns={'timestamp': 'timestamp', 'fundingRate': 'fundingRate','mark_price':'mark_price','index_price':'index_price'})

    # Filter data between the specified start  timestamps
    df1 = df1[(df1['timestamp'] <= start_timestamp*1000)]

    #sort by timestamp in ascending order
    df1 = df1.sort_values(by='timestamp')

    #reset it's index
    df1 = df1.reset_index(drop=True)

    # Select the last two rows
    last_two_rows = df1.tail(2)

    # Calculate the time difference between the last two timestamps
    time_diff = last_two_rows['timestamp'].diff().iloc[-1]

    # Check if the time difference is approximately 8 hours (28800 seconds)
    is_approx_8_hours = abs(time_diff - 28800000) <= 10000


        # Check if the group meets the condition
    if len(df1)>=299 and is_approx_8_hours :

        # If it doesn't meet the condition, drop the group from the original DataFrame
        df_final[symbol]=group[-299:]

print(df_final)



{'BTC/USDT:USDT':      Unnamed: 0         symbol  fundingRate      timestamp  \
1             1  BTC/USDT:USDT       0.0100  1707091200000   
2             2  BTC/USDT:USDT       0.0100  1707120000000   
3             3  BTC/USDT:USDT       0.0100  1707148800000   
4             4  BTC/USDT:USDT       0.0100  1707177600000   
5             5  BTC/USDT:USDT       0.0067  1707206400001   
..          ...            ...          ...            ...   
295         295  BTC/USDT:USDT       0.0100  1715558400001   
296         296  BTC/USDT:USDT       0.0085  1715587200001   
297         297  BTC/USDT:USDT       0.0092  1715616000000   
298         298  BTC/USDT:USDT       0.0099  1715644800000   
299         299  BTC/USDT:USDT       0.0100  1715673600000   

                     datetime  index_price  mark_price  
1    2024-02-05T00:00:00.000Z      43059.0    43071.88  
2    2024-02-05T08:00:00.000Z      42629.7    42644.03  
3    2024-02-05T16:00:00.000Z      42692.9    42708.70  
4    2024

# Function For Long Term Moving Average
 **T** Represent **8** hr period

In [27]:
#For Long Term Moving Average
def CalLongTerm(T):

    if(T==3 or T==9 or T==15 or T==21):
        #For days 1 3 5  7
        return 30
    elif(T==30 or T==63):
        #For day 10 14 
        return 45
    else:
         #For days 21,28
        return 45


# Function For Short Term Moving Average

 **T** Represent **8** hr period

In [28]:
#For Short Term Moving Average
def CalShortTerm(T):
    if(T==3 or T==9 or T==15 or T==21):
      #For days 1 3 5 7
        return 3
    elif(T==30):
      #For days 10
        return 6
    elif(T==63 or T==42):
     #For days 14 21
        return 6
    else:
     #For days 28
        return 9

# Function For Transition Rate

 **T** Represent **8** hr period

In [29]:
#For Alpha (Rate of transition)
def CalAlpha(T):
   #Transtion Rate btw R_0 and R_INF
    if(T==3 or T==9 or T==15):
       #for Day 1 3 5
       return -1.0
    elif(T==21):
       #for Day 7
       return -0.75
    elif(T==30):
       #for Day 10
       return -0.5
    elif(T==63 or T==42):
      #for Day 14 21
       return -0.2
    else:
      #for Day  28
       return -0.1

# Basic Model Function

In [30]:
#Prediction Function Based on Given Parameters
def predicted_value(T,alpha_estimate,R_0,R_inf,half_time):

# Calculate the predicted funding rates based on the estimated alpha
    i_test = np.arange(1,1+T)  # Adjust the index range

    predicted_funding_rate = R_0 * np.exp(alpha_estimate * ((i_test*8)/(half_time*24.0))) + R_inf * (1 - np.exp(alpha_estimate * ((i_test*8)/(half_time*24.0))))

# # Create a DataFrame with the 'predicted_funding_rate' and the new index
    index_starting_from_0 = np.arange(0, 0 + len(predicted_funding_rate))
    predicted_df = pd.DataFrame({'predicted_funding_rate': predicted_funding_rate}, index=index_starting_from_0)

    return  (predicted_funding_rate)

# Ornstein Uhlenbeck Model Function

In [31]:
def ornstein_uhlenbeck_model_1(df,T,mean,t,s):

    np.random.seed(seed=42)

    N =  T #time steps
    paths =10 # number of paths
    T_1 = T/3
    T_vec, dt = np.linspace(0, T_1, N, retstep=True)

#Assign parameters For Model
    theta=mean
    kappa=0
    if(T==42 or T==63 or T==84):
        #For Days 14 21 28
        kappa=0.4
    else:
        #For Days 1 3 5 7 10
        kappa=1.4
    sigma=s

    std_asy = np.sqrt(sigma**2 / (2 * kappa))  # asymptotic standard deviation

    X0 = df['fundingRate'].iloc[-T]
    # print(X0)
    X = np.zeros((paths, N))
    X[:, 0] = X0
    W = ss.norm.rvs(loc=0, scale=1, size=(paths, N - 1))

    std_dt = np.sqrt(sigma**2 / (2 * kappa) * (1 - np.exp(-2 * kappa * dt)))
    for t in range(0, N - 1):
        X[:, t + 1] = theta + np.exp(-kappa * dt) * (X[:, t] - theta) + std_dt * W[:, t]

    # # Calculate mean at each time point and store in X_T
    X_T = np.zeros(X.shape[1])  # Assuming X has shape (paths, N)
    for t in range(X.shape[1]):
        data=X[:, t]
        
        # Check for non-finite values
        if not np.isfinite(data).all():
        # Replace non-finite values with zeros
           data = np.nan_to_num(data)

        param = ss.norm.fit(data)  # FIT from data at each time point
        X_T[t] = param[0] # Store the mean parameter

    return X_T

# Average Projected Funding Rate :

In [32]:
def avg_projected_funding_Rate(df,T):
    df_1=df['fundingRate']

    #Fetching Historical Data For calutlation of avg projected funding rate
    df_2=df_1.values[-T:]
    realzing_funding_rate=np.mean(df_2)

    return realzing_funding_rate

# Evalution Metrics Function

In [33]:
def evalution_mertrics(df,T,R_0,R_inf,half_time,alpha_estimate,df_funding):
    import numpy as np
    from scipy import stats

    df_test=df['fundingRate']
    df_funding=df_funding[-T:]


#Fetching Historical Data For calutlation parameters of Evalution Mertrics
    df_test_1=df_test.values[-T:]
    realzing_funding_rate=np.mean(df_test_1)

    df_1= df_test.rolling(window=R_0).mean()
    df_2= df_test.rolling(window=R_inf).mean()
    R_0_1=df_1.iloc[-(T+1)]
    R_inf_1=df_2.iloc[-(T+1)]

#Predicting Future Value on back Data For Evaluating different paramters
    predicted_funding=predicted_value(T,alpha_estimate,R_0_1,R_inf_1,half_time)

    predicted_funding_rate=np.mean(predicted_funding)

    predicted_value_1=ornstein_uhlenbeck_model_1(df,T,predicted_funding_rate,0,np.std(np.std(df_funding[-15:])))
    predicted_funding_value=np.mean(predicted_value_1)

    if(T==3 or T==9 or T==15):
       predicted_value_1=predicted_funding
       predicted_funding_value=predicted_funding_rate

#Annualising Factor
    ann_factor=3*365

#Calculating Delta
    delta=abs(realzing_funding_rate-predicted_funding_value)

#Calculating Realtive Delta
    relative_delta=abs(realzing_funding_rate-predicted_funding_value)/abs(realzing_funding_rate)
    relative_delta=relative_delta*100

    # print(predicted_funding_value,realzing_funding_rate)
# Extract the actual and predicted funding rates as NumPy arrays
    actual_funding = df_test_1

    coorelation=0.0
# Calculate the correlation between actual and predicted funding rates
    with np.errstate(invalid='ignore'):
         coorelation = np.corrcoef(actual_funding,predicted_value_1)[0, 1]

    if np.isnan(coorelation):
       coorelation = 0.0
    beta=0
# Calculate the beta (capture) between actual and predicted funding rates
    if np.all(predicted_value_1 == predicted_value_1[0]):
       beta=0
        # print("All x-values are identical. Linear regression cannot be calculated.")
    else:
        slope, intercept, r_value, p_value, std_err = stats.linregress(predicted_value_1, actual_funding)
        beta = slope

    return relative_delta,delta,beta,coorelation

# Funding Rate Projection Function

In [34]:
#Function used to set parameters after that Run all function and Give Results
def funding_rate_projection(df,T,R_0,R_inf,half_time,df_funding,alpha):

#Extract Data For Projection
    df_train=df

    df_1= df_train['fundingRate'].rolling(window=R_0).mean()
    df_2= df_train['fundingRate'].rolling(window=R_inf).mean()
    R_0_1=df_1.iloc[-1]
    R_inf_1=df_2.iloc[-1]

    #Predicting Future Value of funding rate in real time
    predicted_funding_rate=predicted_value(T,alpha,R_0_1,R_inf_1,half_time)

    #Round of Value of Funding Rate Upto 5 decimal
    predicted_funding=np.round(predicted_funding_rate, decimals=7)

    #Pass Predicted Funding Rate form basic Model To ou Model For Further Calibration
    predicted_funding_value=ornstein_uhlenbeck_model_1(df,T,np.mean(predicted_funding),1,np.std(df_funding[-15:]))


    #For Day 1 3 5 use Basic Model for other Tenors use Basic Model + Osterin Uhlenbeck Model
    if(T==3 or T==9 or T==15 or  (predicted_funding_value == 0).any()):
       return predicted_funding
    else:
       return predicted_funding_value

# Dashbord Projected Funding Rate

In [36]:
def dashboard_Ann(server,table_name,df_symbol,df):
    import dash
    from dash import html, dcc, Input, Output, State
    from dash.dash_table import DataTable
    import pandas as pd
    import numpy as np
    from datetime import datetime

    # Get the time when the table was created
    table_creation_time = datetime.now()


    # Initialize the Dash app
    app = dash.Dash(__name__)



    # Define the dashboard layout
    app.layout = html.Div([
        html.H1(f'{table_name} Values Table'),

        # Dropdown for selecting symbols
        html.Label('Select Symbol(s)'),
        dcc.Dropdown(
            id='symbol-dropdown',
            options=[{'label': symbol, 'value': symbol} for symbol in df_symbol],
            value=[],  # Default: no symbols selected
            multi=True
        ),

        # Checkbox for annualized values
        html.Label('Non Annualized'),
        dcc.Checklist(
            id='annualize-checkbox',
            options=[{'label': 'Non Annualized', 'value': 'annualized'}],
            value=[],
            style={'margin-bottom': '10px'}
        ),

        # Button to reset the selection
        html.Button('Reset', id='reset-button', n_clicks=0, style={'margin-bottom': '10px'}),

        DataTable(
            id='delta-table',
            columns=[
                {'name': col, 'id': col} for col in df.columns
            ],
            data=df.to_dict('records'),  # Populate the table with data
            page_size=20,  # Adjust the number of rows per page as needed
            style_table={'height': '500px', 'overflowY': 'auto'}
        )

    ])


    # Callback to update the table data based on selected symbols and the checkbox
    @app.callback(
        [Output('delta-table', 'data'),
        Output('symbol-dropdown', 'value'),
        Output('annualize-checkbox', 'value')],
        [Input('symbol-dropdown', 'value'),
        Input('annualize-checkbox', 'value'),
        Input('reset-button', 'n_clicks')],
        State('annualize-checkbox', 'value'),
        prevent_initial_call=True
    )
    def update_table(selected_symbols, annualized, reset_clicks, prev_annualized_value):
        changed_id = [p['prop_id'] for p in dash.callback_context.triggered][0]

        # If the reset button is clicked, reset the dropdown and annualized checkbox
        if 'reset-button' in changed_id:
            return df.to_dict('records'), [], []

        # Update the annualized checkbox value if it has changed
        if annualized != prev_annualized_value:
            prev_annualized_value = annualized

        if not selected_symbols:
            return [], selected_symbols, prev_annualized_value

        # Filter DataFrame based on selected symbols
        filtered_df = df[df['symbol'].isin(selected_symbols)]

        # If 'Non Annualized' is checked, divide the data by 3*365
        if 'annualized' in annualized:
            filtered_df_annualized = filtered_df.copy()
            filtered_df_annualized.iloc[:, 1:] /= (3 * 365)
            return filtered_df_annualized.to_dict('records'), selected_symbols, prev_annualized_value
        else:
            return filtered_df.to_dict('records'), selected_symbols, prev_annualized_value

    app.run_server(debug=True,port=server)
    return



# Dashbord For Yield Curve

In [37]:
def dashboard_Yield(server,df_symbol,df,live_projected_rates):
    import dash
    from dash import html, dcc, Input, Output, State
    import pandas as pd
    import plotly.graph_objs as go

    # Get the time when the table was created
    table_creation_time = datetime.now()


    # Initialize the Dash app
    app = dash.Dash(__name__)

    # Define the dashboard layout
    app.layout = html.Div([
        html.H1('Yeild Curves'),

        # Dropdown for selecting symbols
        html.Label('Select Symbol(s)'),
        dcc.Dropdown(
            id='symbol-dropdown',
            options=[{'label': symbol, 'value': symbol} for symbol in df_symbol],
            value=[],  # Default: no symbols selected
            multi=True
        ),

        # Button to reset the selection
        html.Button('Reset', id='reset-button', n_clicks=0, style={'margin-bottom': '10px'}),

        # Graph to display annualized delta values
        dcc.Graph(id='annualized-graph'),
    ])

    # Callback to update the graph based on selected symbols
    @app.callback(
        Output('annualized-graph', 'figure'),
        [Input('symbol-dropdown', 'value')],
        prevent_initial_call=True
    )
    def update_graph(selected_symbols):
        # Check if no symbols selected
        if not selected_symbols:
            return go.Figure()

        filtered_data = {symbol: live_projected_rates[symbol] for symbol in selected_symbols}

        # Create traces for each selected symbol
        traces = []
        for symbol, values in filtered_data.items():
            annualized_values = [val * ( 3 * 365 ) for val in values]
            traces.append(go.Scatter(x=df.columns[1:], y=annualized_values, mode='lines', name=symbol))

        layout = go.Layout(
            title='Annualized Delta Values vs Days',
            xaxis=dict(title='Days'),
            yaxis=dict(title='%ANN'),
        )

        return {'data': traces, 'layout': layout}

    app.run_server(debug=True,port=server)
    return

# Genralize Function For Projection

In [38]:
#Function That Stores Fundinig Rate prediction of All perpetual contract
def Genralize_Model_Projection(df_final):



        #Creating Empty dataframe
        time_periods =['Day1','Day3','Day5','Day7','Day10','Day14','Day21','Day28']
        columns = ['symbol'] +time_periods
        df1 = pd.DataFrame(columns=columns)



        ####-------------- Define data frame df_t_1 ----------------###########

        # Extracting the symbols
        symbols = df_final.keys()

        # Creating a DataFrame with the symbols
        df_t_1 = pd.DataFrame({'symbol': symbols})

        ####-------------- Define data frame df_t_1 ----------------###########

        # Set the 'Symbol' column in df1 to be the same as in df
        df1['symbol'] = df_t_1['symbol']

        i=0
        #Tranversing over every Perpetual contract
        for symbol, group in zip(df_final.keys(), df_final.values()):

            #create array of different-different Time periods as 8hrs
            time_period=[3,9,15,21,30,42,63,84]

            half_time=2.0

            ####-------------------------------------------- CHANGE ----------------------------------------------------------###

            df=group

            #swap History data for SYMBOL
            df_price=df['index_price']
            
            #spot History data for SYMBOL
            df_price_1=df['mark_price']

            ####-------------------------------------------- CHANGE ----------------------------------------------------------###


            df_funding=(df_price-df_price_1)*100/df_price_1

            a=np.array([1,3,5,7,10,14,21,28])

            j=0

            projected_rates=[]
            projected_rates_sum=[]
            
            #for particular Perpertual Predicting For Different Time periods
            for periods in time_period:

                #Calculating R_0 and R_inf Different for Different Time period
                R_inf=CalLongTerm(periods)
                R_0=CalShortTerm(periods)
                alpha=CalAlpha(periods)

                #Predicting Funding Rate for particular time period and perpetual
                predicted_funding_rate=funding_rate_projection(df,periods,R_0,R_inf,half_time,df_funding,alpha)
                
                #Mean of predicted Funding Rate
                predicted_value=np.mean(predicted_funding_rate)

                predicted_value=np.round(predicted_value, decimals=5)




                df1.iloc[i, df1.columns.get_loc(f'Day{(a[j])}')]=predicted_value*3*365
                projected_rates.append(predicted_value)
                projected_rates_sum.append(fwd_sum(predicted_funding_rate,periods))


                j=j+1
            projected_fwd[symbol]=projected_rates
            projected_fwd_sum[symbol]=projected_rates_sum            
            i=i+1
            print(i)

        df1= df1.reset_index(drop=True)


        #Assign Server Port Different Dashboard
        
        dashboard_Ann(5600,'Project Funding',df_symbol,df1)
        dashboard_Yield(5606,df_symbol,df1,projected_fwd)

        #Saving CSV file for Dataframe
        df1.to_csv('Prediction_Funding_Rate.csv') 

        return

# Run For Model Projection AND  Yield Curve

In [39]:
#Run function Genralized Model over different perpetual Contracts to get prediction on real time
Genralize_Model_Projection(df_final)

1


# Dashbord For Beta ,Coorelation , Relative Delta

In [60]:


def dashboard(server, table_name, df_symbol, df):
    import dash
    from dash import html, dcc, Input, Output, State
    from dash.dash_table import DataTable
    import pandas as pd
    from datetime import datetime
    # Get the time when the table was created
    table_creation_time = datetime.now()

    # Initialize the Dash app
    app = dash.Dash(__name__)

    # Define the dashboard layout
    app.layout = html.Div([
        html.H1(f'{table_name} Values Table'),

        # Dropdown for selecting symbols
        html.Label('Select Symbol(s)'),
        dcc.Dropdown(
            id='symbol-dropdown',
            options=[{'label': symbol, 'value': symbol} for symbol in df_symbol],
            value=[],  # Default: no symbols selected
            multi=True
        ),

        # Button to reset the selection
        html.Button('Reset', id='reset-button', n_clicks=0, style={'margin-bottom': '10px'}),

        DataTable(
            id='delta-table',
            columns=[
                {'name': col, 'id': col} for col in df.columns
            ],
            data=df.to_dict('records'),  # Populate the table with data
            page_size=20,  # Adjust the number of rows per page as needed
            style_table={'height': '500px', 'overflowY': 'auto'}
        )
    ])

    # Callback to update the table data based on selected symbols
    @app.callback(
        [Output('delta-table', 'data'),
         Output('symbol-dropdown', 'value')],
        [Input('symbol-dropdown', 'value'),
         Input('reset-button', 'n_clicks')],
        prevent_initial_call=True
    )
    def update_table(selected_symbols, reset_clicks):
        changed_id = [p['prop_id'] for p in dash.callback_context.triggered][0]

        # If the reset button is clicked, reset the dropdown
        if 'reset-button' in changed_id:
            return df.to_dict('records'), []

        if not selected_symbols:
            return [], selected_symbols

        # Filter DataFrame based on selected symbols
        filtered_df = df[df['symbol'].isin(selected_symbols)]
        return filtered_df.to_dict('records'), selected_symbols

    app.run_server(debug=True, port=server)
    return


# Genralize Function For Projection

In [61]:
#Function That Stores Fundinig Rate prediction of All perpetual contract
def Genralize_Model_Evalution(df_final):


        #dict to store live projected rates for all symbols
        projected_fwd={}


        #Creating Empty dataframe
        time_periods =['Day1','Day3','Day5','Day7','Day10','Day14','Day21','Day28']
        columns = ['symbol'] +time_periods
        df1 = pd.DataFrame(columns=columns)
        df2 = pd.DataFrame(columns=columns)
        df3 = pd.DataFrame(columns=columns)
        df4 = pd.DataFrame(columns=columns)


        ####-------------- Define data frame df_t_1 ----------------###########

        # Extracting the symbols
        symbols = df_final.keys()

        # Creating a DataFrame with the symbols
        df_t_1 = pd.DataFrame({'symbol': symbols})

        ####-------------- Define data frame df_t_1 ----------------###########

        # Set the 'Symbol' column in df1 to be the same as in df
        df1['symbol'] = df_t_1['symbol']
        df2['symbol'] = df_t_1['symbol']
        df3['symbol'] = df_t_1['symbol']
        df4['symbol'] = df_t_1['symbol']

        i=0
        #Tranversing over every Perpetual contract
        for symbol, group in zip(df_final.keys(), df_final.values()):

            #create array of different-different Time periods as 8hrs
            time_period=[3,9,15,21,30,42,63,84]

            half_time=2.0

            ####-------------------------------------------- CHANGE ----------------------------------------------------------###

            df=group

            #swap History data for SYMBOL
            df_price=df['index_price']

            #spot History data for SYMBOL
            df_price_1=df['mark_price']

            ####-------------------------------------------- CHANGE ----------------------------------------------------------###


            df_funding=(df_price-df_price_1)*100/df_price_1
            
            
            a=np.array([1,3,5,7,10,14,21,28])

            j=0

            projected_rates=[]
            #for particular Perpertual Predicting For Different Time periods
            for periods in time_period:

                #Calculating R_0 and R_inf Different for Different Time period
                R_inf=CalLongTerm(periods)
                R_0=CalShortTerm(periods)
                alpha=CalAlpha(periods)
                
                #Calculating Different Parameters of evalution mertrics
                relative_delta,delta,beta,coorelation=evalution_mertrics(df,periods,R_0,R_inf,half_time,alpha,df_funding)


                delta=np.round(delta, decimals=5)
                relative_delta=np.round(relative_delta, decimals=3)
                coorelation=np.round(coorelation, decimals=3)
                beta=np.round(beta, decimals=4)


                df1.iloc[i, df1.columns.get_loc(f'Day{(a[j])}')] = delta*3*365
                df2.iloc[i, df2.columns.get_loc(f'Day{(a[j])}')] = beta
                df3.iloc[i, df3.columns.get_loc(f'Day{(a[j])}')] = coorelation
                df4.iloc[i, df4.columns.get_loc(f'Day{(a[j])}')] = relative_delta


                j=j+1

            i=i+1
            print(i)

        df1= df1.reset_index(drop=True)
        df2= df2.reset_index(drop=True)
        df3= df3.reset_index(drop=True)
        df4= df4.reset_index(drop=True)


        #Assign Server Port Different Dashboard
        dashboard_Ann(5602,'Absolute Delta ',df_symbol,df1)
        dashboard(5603,'Beta ',df_symbol,df2)
        dashboard(5604,'Coorelation ',df_symbol,df3)
        dashboard(5605,'Relative Delta ',df_symbol,df4)


        #Saving CSV file for Dataframe
        # df1.to_csv('Absolute_Delta.csv') 
        # df4.to_csv('Relative_Delta.csv')
        # df2.to_csv('Beta.csv')
        # df3.to_csv('Coorelation.csv')

# Run For Evalution Metrics

In [62]:
#Run function Genralized Model over different perpetual Contracts to get Evaluation on real time
Genralize_Model_Evalution(df_final)

1
2


# Genralize Function For Historical Averages

In [26]:
#Function That Stores Fundinig Rate prediction of All perpetual contract
def Genralize_Model_Average(df_final):


        #dict to store live projected rates for all symbols
        projected_fwd={}


        #Creating Empty dataframe
        time_periods =['Day1','Day3','Day5','Day7','Day10','Day14','Day21','Day28']
        columns = ['symbol'] +time_periods
        df1 = pd.DataFrame(columns=columns)


        ####-------------- Define data frame df_t_1 ----------------###########

        # Extracting the symbols
        symbols = df_final.keys()

        # Creating a DataFrame with the symbols
        df_t_1 = pd.DataFrame({'symbol': symbols})

        ####-------------- Define data frame df_t_1 ----------------###########

        # Set the 'Symbol' column in df1 to be the same as in df
        df1['symbol'] = df_t_1['symbol']


        i=0

        #Tranversing over every Perpetual contract
        for symbol, group in zip(df_final.keys(), df_final.values()):

            #create array of different-different Time periods as 8hrs
            time_period=[3,9,15,21,30,42,63,84]
             
            #Define Name of Group As Df
            df=group

            j=0



            a=np.array([1,3,5,7,10,14,21,28])

            #for particular Perpertual Predicting For Different Time periods
            for periods in time_period:

                
                avg_projected_funding=avg_projected_funding_Rate(df,periods)
                
              
                #Mean of Historical Averages
                avg_projected=np.mean(avg_projected_funding)

                avg_projected=np.round(avg_projected, decimals=5)

                df1.iloc[i, df1.columns.get_loc(f'Day{(a[j])}')] = avg_projected*3*365


                j=j+1

            i=i+1
            print(i)

        df1= df1.reset_index(drop=True)

        #Assign Server Port Different Dashboard
        dashboard_Ann(5601,'Average Funding',df_symbol,df1)
 

        #Saving CSV file for Dataframe
        # df1.to_csv('Average_Funding_Rate.csv') 

# Run For Historical Averages

In [27]:
#Run function Genralized Model over different perpetual Contracts to get Average on real time
Genralize_Model_Average(df_final)


1
